# Final Exam review

## How to post the answers in the jupyter notebook.

- The final exam should be completed on your virtual desktop, and reported in jupyter notebook.
- Jupyter notebook installation on the virtual desktop was discussed in the previous lecture.

Create directory `Final` in your home directory on the virtual desktop:
```bash
mkdir Final
```

Download the exam ipynb file into directory Final:
```bash
cd Final
wget http://capone.rutgers.edu/coursefiles/Final_exam_preparation.ipynb
```
Copy the `ipynb` file into your desktop#.ipynb:
```bash
cp Final_exam_preparation.ipynb $(uname -n)-final.ipynb
```
Restart the jupyter notebook on your desktop:
```bash
pkill -9 jupyter-notebook
jupyter notebook &
```
Access jupyter notebook through the browser on your virtual desktop by navigating to URL below:
```c
http://localhost:8888
```

Navigate to folder `Final`. Open your desktop `ipynb` file, for example
`desktop16-final.ipynb`

Complete the final exam exercises. In the beginning and the end, execute the clock in and clock out cells, accordingly.

<hr>

## Final Exam 2021 sample

The exercises are supposed to be done by each student solely on his/her desktop in the Linux lab, D-112. It is allowed to use the lecture notes at https://linuxcourse.rutgers.edu, any printed material, as well as internet published resources.
Number of exercises: 5. Each exercise has a maximum score.

You can do the exam continuously for 3 hrs at any time between Thursday 7/8/21 morning time and Friday 7/9/21 before midnight. There are clock in and clock out scripts to start and submit the exam.  

Please put your name in the cell below. 
Execute the python script in the cell below to clock in when you start working on the exam. When you are done, execute the cell with `exam_end()` at the bottom to submit your work. If you submit it multiple times, only the last one will be greaded. 

- Your name:  Alexei 
- Your desktop number: desktop01

In [3]:
#Execute the cell for exam start date and time:
from datetime import datetime
now = datetime.now()
dt_string_start = now.strftime("%d/%m/%Y %H:%M")
print('Exam Start:', dt_string_start)

Exam Start: 07/07/2021 21:23


## 1. Port scan (max score 4)
- A) Download final2020.tgz from http://capone.rutgers.edu/coursefiles/final2020.tgz by using command wget, and deploy final2020 VM on your desktop.
- B) By using command lsof on the VM find out what network services are running, what processes IDs (PIDs) they have, and what ports they open.
- C) Find out the IP address of the VM.
By using command nmap on the desktop, run TCP port scan for final2020 VM.

<hr>

- Answer:

A)

```bash
wget  http://capone.rutgers.edu/coursefiles/final2020.tgz

tar -zxvf final2020.tgz 

mv final2020.qcow2 KVM/

sudo cp final2020.xml /etc/libvirt/qemu

virsh define /etc/libvirt/qemu/final2020.xml
```

 
B)
```
 root@final2020:~# lsof -i -P
COMMAND   PID            USER   FD   TYPE DEVICE SIZE/OFF NODE NAME
systemd-n 251 systemd-network   20u  IPv4  13945      0t0  UDP final2020:68 
systemd-r 256 systemd-resolve   12u  IPv4  12264      0t0  UDP localhost:53 
systemd-r 256 systemd-resolve   13u  IPv4  12265      0t0  TCP localhost:53 (LISTEN)
vsftpd    279            root    3u  IPv6  13135      0t0  TCP *:21 (LISTEN)
sshd      280            root    3u  IPv4  13238      0t0  TCP *:22 (LISTEN)
sshd      280            root    4u  IPv6  13249      0t0  TCP *:22 (LISTEN)
lighttpd  283        www-data    6u  IPv4  13663      0t0  TCP *:80 (LISTEN)
lighttpd  283        www-data    7u  IPv4  13664      0t0  TCP *:443 (LISTEN)

```
 C) 
```
ip a
```
192.168.122.10

```
root@desktop01:~# nmap -sT 192.168.122.10

Starting Nmap 7.60 ( https://nmap.org ) at 2021-07-07 18:36 EDT
Nmap scan report for 192.168.122.10
Host is up (0.000056s latency).
Not shown: 996 closed ports
PORT    STATE SERVICE
21/tcp  open  ftp
22/tcp  open  ssh
80/tcp  open  http
443/tcp open  https
MAC Address: 52:54:00:0B:94:F0 (QEMU virtual NIC)
```


 

## 2. Iptables (max score 6)
- A) On the VM, deploy iptables rules to allow SSH and https access from anywhere, while  ftp and http  from your desktop only.  All other ports should be closed.
- B) Scan the VM with nmap again to verify that the `SSH, ftp, http, https`, and `ftp` ports are open for the desktop.
- C) Start another VM you have, for example, testub. Install nmap on the VM, and scan the TCP ports for final2020. Verify that only SSH and https ports are open.
- D) On the VM, flush the iptables rules and redefine the default policy to ACCEPT.
Scan the ports on the VM from testub to make sure they are open.

<hr>

- Answer:

A)
```
#!/bin/bash

iptables -P INPUT DROP
iptables -P OUTPUT ACCEPT
iptables -P FORWARD DROP

iptables -F

iptables -A INPUT -p tcp --dport 22 -j ACCEPT
iptables -A INPUT -p tcp --dport 443 -j ACCEPT
iptables -A INPUT -p icmp -j ACCEPT
iptables -A INPUT -p tcp --dport 21 -s 192.168.122.1 -j ACCEPT
iptables -A INPUT -p tcp --dport 80 -s 192.168.122.1 -j ACCEPT

```

B)
```
root@desktop01:~# nmap -sT 192.168.122.10

Starting Nmap 7.60 ( https://nmap.org ) at 2021-07-07 18:58 EDT
Nmap scan report for 192.168.122.10
Host is up (0.00032s latency).
Not shown: 996 filtered ports
PORT    STATE SERVICE
21/tcp  open  ftp
22/tcp  open  ssh
80/tcp  open  http
443/tcp open  https
MAC Address: 52:54:00:0B:94:F0 (QEMU virtual NIC)

Nmap done: 1 IP address (1 host up) scanned in 4.92 seconds
```

C)
```
root@testub:~# nmap -sT 192.168.122.10

Starting Nmap 7.60 ( https://nmap.org ) at 2021-07-07 19:00 EDT
Nmap scan report for final2020 (192.168.122.10)
Host is up (-0.12s latency).
Not shown: 998 filtered ports
PORT    STATE SERVICE
22/tcp  open  ssh
443/tcp open  https
MAC Address: 52:54:00:0B:94:F0 (QEMU virtual NIC)

Nmap done: 1 IP address (1 host up) scanned in 4.77 seconds
```

D)
```
iptables -P INPUT ACCEPT
iptables -F
```

## 3. Shell scripts (max score 4)

- Below are two shell scripts.
Script `send.sh`

```bash
#!/bin/bash 
ipaddr='192.168.122.11' 
port='9092' 
echo "provide input file name" 
read fname 
/bin/cat "$fname" | /bin/netcat -N "$ipaddr" $port
```

- and script receive.sh:
```bash
#!/bin/bash 
DIR='/home/hostadm' 
fname='fileget.out' 
port='9092' 
if [ -s "$DIR/$fname" ] 
then 
echo 'file exists' 
else 
/bin/netcat -N -l "$port" > "$DIR/$fname" 
fi
```

- A) What do the scripts do?
- B) Put script receive.sh on final2020 VM.
Put script send.sh on the desktop, and modify variable ipaddr in the script to match the IP address of final2020.
Run both the scripts to send/receive a file between the desktop and final2020 VM.

- Answer:
```
A) send.sh sends data over netcat, receive.sh receives data from netcat, and stores into fileget.out.
B)  chmod a+X send.sh, chmod a+x receive.sh, ./receive.sh on final2020.   ./send.sh on the desktop
```



## 4. Static and shared libraries. Header files. (max score 4)

- Install package `libgpg-error-dev` on your desktop.
- What are the file names that contain static libraries, dynamic libraries, and header files in the package?
- Specify the commands you used to find the file names.

- Answer:

```bash
root@desktop01:~# dpkg -L libgpg-error-dev | grep '\.a'
/usr/lib/x86_64-linux-gnu/libgpg-error.a
root@desktop01:~# dpkg -L libgpg-error-dev | grep '\.so'
/usr/lib/x86_64-linux-gnu/libgpg-error.so
root@desktop01:~# dpkg -L libgpg-error-dev | grep '\.h'
/usr/include/x86_64-linux-gnu/gpg-error.h
/usr/include/x86_64-linux-gnu/gpgrt.h
```


In [6]:
#print('Exam Start:', dt_string_start)
#Execute the cell for exam end date and time:
from datetime import datetime
now_end = datetime.now()
dt_string = now_end.strftime("%d/%m/%Y %H:%M")
print('Exam End:', dt_string)

Exam End: 07/07/2021 21:25


<hr>

## Exercises for final exam preparation

## 5. Shell scripting

- Consider the following script:
```bash
#!/bin/bash
cmmd= /usr/bin/md5sum
for i in $(ls /etc); do
if [ ! -d  /etc/$i ] then
$cmmd /etc/$i
fi
done
```

It fails to run due to a few syntactic errors.

- A) Find the errors in the script.
- B) Explain what the script does.



- Answer:

A) Fixed script:
```
#!/bin/bash
cmmd=/usr/bin/md5sum
for i in $(ls /etc); do
if [ ! -d  /etc/$i ]
then
$cmmd /etc/$i
fi
done

```

B) Computes md5sun hashes on the files in /etc directory.


## 6. Task scheduling

- A) Schedule the script to run once on July 9 at 11 pm.
- B) Schedule the script to run every Wednesday at 10:15 AM.

- Answer: 

A)
```bash
at -f /home/hostadm/script.sh  2215 Jul 9
```

B) in /etc/crontab, add:
```
15 10  * * 3   root  /home/hostadm/script.sh
```

## 7. Static and shared libraries

- Install package libgsl-dev on your desktop.
- What are the file names that contain static and dynamic libraries in the package?

- Answer:

```bash
root@desktop01:~# dpkg -L libgsl-dev | grep '\.a'
/usr/lib/x86_64-linux-gnu/libgsl.a
/usr/lib/x86_64-linux-gnu/libgslcblas.a
root@desktop01:~# dpkg -L libgsl-dev | grep '\.so'
/usr/lib/x86_64-linux-gnu/libgsl.so
/usr/lib/x86_64-linux-gnu/libgslcblas.so
```

## 9. Password cracking

- Below are user accounts.
```
basy:$1$saltsalt$9WRUUPoE8YGh.hHkKg/EP1
jim:$1$saltsalt$RMHBY/dfOK.dm9QkTY5KM1
sam:$1$saltsalt$4OYf3FzwaLsHVuINLQZDK.
```
- A) What encryption algorithm was used to generate the hashes?
- B) What is the salt?
- C) Try using John the Ripper to crack the hashes.

- Answer:

A)  md5

B)   saltsalt

C)
```bash
/usr/sbin/john passwords.txt 
Created directory: /home/hostadm/.john
Loaded 3 password hashes with no different salts (md5crypt [MD5 32/64 X2])
Press 'q' or Ctrl-C to abort, almost any other key for status
security         (jim)
awesome          (sam)
admin1           (basy)
3g 0:00:00:00 100% 2/3 7.894g/s 13928p/s 13928c/s 29244C/s admin..admin1
Use the "--show" option to display all of the cracked passwords reliably
Session completed


```


## 10. Port scanning

- Download a VM from http://capone.rutgers.edu/coursefiles/midterm_VM.tgz

Deploy the VM.
- A) On the VM, install the following packages: lighttpd, vsftpd, rpcbind, openssh-server.
- B) On the desktop, run nmap scanner to see the open ports on the VM.

- Answer:

A)  apt install lighttpd vsftpd rpcbind openssh-server

B) nmap -sT 192.168.122.10
```
Starting Nmap 7.60 ( https://nmap.org ) at 2021-07-07 19:32 EDT
Nmap scan report for 192.168.122.10
Host is up (0.000071s latency).
Not shown: 996 closed ports
PORT    STATE SERVICE
21/tcp  open  ftp
22/tcp  open  ssh
80/tcp  open  http
443/tcp open  https
MAC Address: 52:54:00:0B:94:F0 (QEMU virtual NIC)

```
nmap -sU 192.168.122.10

```
#!/bin/bash

iptables -P INPUT DROP
iptables -P OUTPUT ACCEPT
iptables -P FORWARD DROP

iptables -F INPUT
iptables -F OUTPUT
iptables -F FORWARD

iptables -A INPUT -p tcp --dport 22 -j ACCEPT

iptables -A INPUT -p tcp --dport 1024:65535 -m state --state ESTABLISHED,RELATET -j ACCEPT
```


## 11.  Iptables

- A) On the VM, deploy iptables rules to allow only SSH access.
- B) Scan the VM with nmap again to verify that only the SSH port is open.


- Answer:

## 12. Clear iptables rules

- On the VM, flush the iptables rules and redefine the default policy to ACCEPT.
- Scan the ports on the VM to make sure they are open.

- Answer:

## 13 NFS mounts

- A) On final2020 VM install NFS server. export directories `/exports/DD1` and `/exports/DD2` to 192.168.122.188
- B) On 192.168.122.188 VM, mount dirextories `/exports/DD1` and `/exports/DD2`.
- C) What users can write in which directories.

- Answer:

A) On final2020, we install the NFS server package:
```bash
apt install nfs-kernel-server
apt install nfs-common
```
In /etc/exports, we put the following:
```
/exports/DD1  192.168.122.188(rw)
/exports/DD2  192.168.122.188(rw)

```
```bash
systemctl restart nfs-kernel-server
```

B) On testub, run command
```bash
apt install nfs-common
```

```bash
showmount -e 192.168.12.10
```
to see what the directories are exported.

Create mounting points:
```bash
mkdir /mnt/DD1
mkdir /mnt/DD2
```
mount the directories:
```bash
mount 192.168.122.10:/exports/DD1  /mnt/DD1
mount 192.168.122.10:/exports/DD2  /mnt/DD2
```
Check if the directories are mounted:
```bash
df -h
```

C) As hostadm
```bash
cd /mnt/DD1
touch file.txt
```
success

As root:
```bash
cd /mnt/DD2
touch file.txt
```
doesn't work
user hostadm can write into directory `/mnt/DD1` 

user root can't write in either `/mnt/DD1` or `/mnt/DD2`
